# Reinforcement Learning control strategies for Electric Vehicles fleet Virtual Power Plants
Thesis based on the development of a RL agent that manages a VPP through EVs charging stations in an household environment. Main optimization objectives of the VPP are: Valley filling, peak shaving and zero resulting load over time. Main action performed to reach objectives are: storage of Renewable energy resources and power push in the grid at high demand times. The development of the Virtual Power Plant environment is based on the ELVIS (Electric Vehicles Infrastructure Simulator) open library from DAI-Labor: https://github.com/dailab/elvis The thesis code is currently available at: (https://github.com/francescomaldonato/RL_VPP_Thesis)

Author: Francesco Maldonato

## VPP simulator Notebook based on EVs arrival, with StableBaselines3 trained model (Recurrent PPO) [35 EVs per week test]

Installing required packages and dependencies

In [1]:
%%capture
!pip install py-elvis==0.2.1
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido==0.2.1

!pip install stable-baselines3[extra]==1.6.1
!pip install stable-baselines==1.6.1
!pip install sb3-contrib==1.6.1
!pip install gym==0.20.0
!pip install -q wandb==0.13.4

In [2]:
#Cloning repository and changing directory
!git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
%cd RL_VPP_Thesis/
%ls

Cloning into 'RL_VPP_Thesis'...
remote: Enumerating objects: 443, done.
remote: Counting objects: 100% (50/50), done.
remote: Compressing objects: 100% (43/43), done.
remote: Total 443 (delta 13), reused 35 (delta 6), pack-reused 393
Receiving objects: 100% (443/443), 178.48 MiB | 25.13 MiB/s, done.
Resolving deltas: 100% (162/162), done.
Checking out files: 100% (219/219), done.
/content/RL_VPP_Thesis
Agent_trainer_notebooks/          RL_VPP_Thesis/
Algorithm_simulator_notebooks/    trained_models/
data/                             VPP_environment.py
EV_experiment_notebooks/          VPP_simulator.ipynb
Hyperparameters_sweep_notebooks/  wandb/
README.md


In [3]:
import yaml
import numpy as np
from gym import Env
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from sb3_contrib import RecurrentPPO #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
#!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.14
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.20.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.14', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.20.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.14\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.20.0\n')


In [4]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

## Load ELVIS YAML config file
Section where the EVs arrival simulation parameters are loaded through the Yaml config file from the 'data/config_builder/' folder.

In [5]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

#case = 'wohnblock_household_simulation_adaptive.yaml' #(loaded by default, 20 EVs arrivals per week with 50% average battery)

#Try different simulation parameters, uncomment below
#case = 'wohnblock_household_simulation_adaptive_10.yaml' #(10 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_15.yaml' #(15 EVs arrivals per week with 50% average battery)
#case = 'wohnblock_household_simulation_adaptive_25.yaml' #(25 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_30.yaml' #(30 EVs arrivals per week with 50% average battery) 
case = 'wohnblock_household_simulation_adaptive_35.yaml' #(35 EVs arrivals per week with 50% average battery) 

with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7f568c26d1d0>Mean parking time: 23.99
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 30
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 30, 'EVs_n_max': 1566, 'mean_park': 23.99, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_ener

In [6]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
env.plot_VPP_input_data()

Output hidden; open in https://colab.research.google.com to view.

In [7]:
env.plot_ELVIS_data()

In [8]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  32122.97 , over-consume=kWh  47977.07 , under-consume=kWh  15854.1 , Total_cost=€  1242.12 , overcost=€  1692.34 , Av.EV_en_left=kWh  100.0 , Charging_events=  1565 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  66.72
Simulating VPP....


### VPP Simulation test with random actions [no model loaded]

In [9]:
episodes = 1
for episode in range(1, episodes+1):
    state = env.reset()
    done = False
    score = 0
    while not done:
        action_masks = get_action_masks(env)
        action = env.action_space.sample()
        
        n_state, reward, done, info = env.step(action)
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [10]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [11]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [12]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [13]:
env.plot_VPP_Elvis_comparison()

In [14]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [15]:
#env.plot_rewards_stats()

In [16]:
env.plot_EVs_kpi()

In [17]:
env.plot_actions_kpi()

In [18]:
env.plot_load_kpi()

In [19]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [20]:
## Wandb login to load models
#In Colab, uncomment below:
# %env "WANDB_DISABLE_CODE" True
# %env "WANDB_NOTEBOOK_NAME" "VPP_simulator.ipynb"
# os.environ['WANDB_NOTEBOOK_NAME'] = 'VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

In [21]:
#Loading training model, from local directory or from wandb previous trainings
RecurrentPPO_path = "trained_models/RecurrentPPO_models/model_RecurrentPPO_"

#model_id = "s37o8q0n"
model_id = "333ckz0i"
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


## Testing dataset VPP Simulation using the loaded trained model

In [ ]:
#TEST Model
episodes = 10
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

#Save the VPP table
VPP_table = env.save_VPP_table(save_path='data/environment_optimized_output/VPP_table.csv')

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  31719.34 , over-consume=kWh  47872.51 , under-consume=kWh  16153.17 , Total_cost=€  1229.53 , overcost=€  1684.28 , Av.EV_en_left=kWh  100.0 , Charging_events=  1565 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  66.72
Simulating VPP....


In [ ]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00  36.549519  33.447124  46.652370  63.009998   
2022-01-01 00:15:00  36.799519  32.879486  46.084732  63.259998   
2022-01-01 00:30:00  37.049519  32.312229  45.517475  63.509998   
2022-01-01 00:45:00  37.299519  31.851261  45.056507  63.759998   
2022-01-01 01:00:00  37.549519  31.380114  44.585358  64.009995   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  64.883125  56.994339  64.643074  89.360092   
2022-06-06 05:00:00  65.971039  56.744339  65.730988  90.448006   
2022-06-06 05:15:00  67.009094  56.494339  66.769043  91.486061   
2022-06-06 05:30:00  68.116943  56.244339  67.876892  92.593910   
2022-06-06 05:45:00  69.155853  55.994339  68.915802  93.632820   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [1, 2, 2, 1]   
2022-01-01 00:15:00  [4695, 4694, 4692, 4693]  [1, 2, 2, 1]   
2022-01-01 00:30:00  [4695, 4694, 4692, 4693]  [1, 2, 2, 1]   
2022-01-01 00:45:00  [4695, 4694, 4692, 4693]  [1, 2, 2, 1]   
2022-01-01 01:00:00  [4695, 4694, 4692, 4693]  [1, 2, 2, 1]   
...                                       ...           ...   
2022-06-06 04:45:00  [5358, 5359, 5357, 5356]  [1, 2, 1, 1]   
2022-06-06 05:00:00  [5358, 5359, 5357, 5356]  [1, 2, 1, 1]   
2022-06-06 05:15:00  [5358, 5359, 5357, 5356]  [1, 2, 1, 1]   
2022-06-06 05:30:00  [5358, 5359, 5357, 5356]  [1, 2, 1, 1]   
2022-06-06 05:45:00  [5358, 5359, 5357, 5356]  [1, 2, 1, 1]   

                                       mask_truth  ev_charged_pwr  \
time                                                                
2022-01-01 00:00:00  [False, False, False, False]        0.000000   
2022-01-01 00:15:00    [False, True, True, False]        2.000000   
2022-01-01 00:30:00    [False, True, True, False]        2.000000   
2022-01-01 00:45:00    [False, True, True, False]        2.000000   
2022-01-01 01:00:00    [False, True, True, False]        2.000000   
...                                           ...             ...   
2022-06-06 04:45:00     [True, False, True, True]        9.895592   
2022-06-06 05:00:00     [True, False, True, True]       13.054952   
2022-06-06 05:15:00    [True, False, True, False]       12.456707   
2022-06-06 05:30:00    [True, False, True, False]       13.294198   
2022-06-06 05:45:00    [True, False, True, False]       12.466959   

                     ev_discharged_pwr          load  load_reward  EV_reward  \
time                                                                           
2022-01-01 00:00:00           0.000000  1.727308e+00         15.0        0.0   
2022-01-01 00:15:00          -4.541117  0.000000e+00         15.0        0.0   
2022-01-01 00:30:00          -4.538057  0.000000e+00         15.0        0.0   
2022-01-01 00:45:00          -3.687741  0.000000e+00         15.0        0.0   
2022-01-01 01:00:00          -3.769187  0.000000e+00         15.0        0.0   
...                                ...           ...          ...        ...   
2022-06-06 04:45:00          -1.000000  0.000000e+00         15.0        0.0   
2022-06-06 05:00:00          -1.000000  0.000000e+00         15.0        0.0   
2022-06-06 05:15:00          -1.000000  1.776357e-15         15.0        0.0   
2022-06-06 05:30:00          -1.000000  1.776357e-15         15.0        0.0   
2022-06-06 05:45:00          -1.000000  0.000000e+00         15.0        0.0   

                     rewards  
time                          
2022-01-01 00:00:00     15.0  
2022-01-01 00:15:00     15.0  
2022-01-01 00:30:00     15.0  
2022-01-01 00:45:00     15.0  
2022-01-01 01:00:00     15.0  
...                      ...  
2022-06-06 04:45:00     15.0  
2022-06-06 05:00:00     15.0  
2022-06-06 05:15:00     15.0  
2022-06-06 05:30:00     15.0  
2022-06-06 05:45:00     15

In [ ]:
#env.plot_Elvis_results()

In [ ]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Validating dataset VPP Simulation using the loaded trained model

In [ ]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 6261, Arrival time: 2022-01-01 09:00:00, Parking_time: 24, Leaving_time: 2022-01-02 09:00:00, SOC: 0.530449438694012, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 7825, Arrival time: 2022-12-31 19:00:00, Parking_time: 24, Leaving_time: 2023-01-01 19:00:00, SOC: 0.6024435577839183, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , over-consume=kWh  2136.67 , under-consume=kWh  -32222.06 , Total_cost=€  -1187.15 , overcost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  22102.57 , over-consume=kWh  42201.66 , under-consume=kWh  20099.08 , Total_cost=€  1005.22 , overcost=€  1824.29 , Charging_events=  1565 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  70.59


In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [ ]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  21828.63 , over-consume=kWh  42605.31 , under-consume=kWh  20776.67 , Total_cost=€  1016.42 , overcost=€  1857.06 , Av.EV_en_left=kWh  100.0 , Charging_events=  1565 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  70.59
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -4079.56 , over-consume=KWh  859.52 , under-consume=KWh  4939.08 , Total_cost=€  -134.16 , Overcost=€  36.47 
 EV_INFO: Av.EV_energy_leaving=kWh  66.38 , Std.EV_energy_leaving=kWh  23.6 , EV_departures =  1562 , EV_queue_left =  0
SCORE:  Cumulative_reward= 472273.15 - Step_rewars (load_t= 412844.17, EVs_energy_t= 22050.72)
 - Final_rewards (EVs_energy= 21823.78, Overconsume= -7.1, Underconsume= -707.29, Overcost= 16268.88)
Episode:1 Score:472273.1508835329


In [ ]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00   0.000000  36.295860   0.000000   0.000000   
2022-01-01 00:15:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:30:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:45:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 01:00:00   0.000000   0.000000   0.000000   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  70.723640  40.805264  50.346348  96.608910   
2022-06-06 05:00:00  71.994789  40.555264  51.617493  97.880058   
2022-06-06 05:15:00  73.315147  40.305264  52.937847  99.200417   
2022-06-06 05:30:00  74.604828  40.055264  54.227528  99.989998   
2022-06-06 05:45:00  75.837303  39.805264  55.460003  99.989998   

                                           EVs_id       actions  \
time                                                              
2022-01-01 00:00:00                  [0, 0, 0, 0]  [0, 1, 2, 2]   
2022-01-01 00:15:00                  [0, 0, 0, 0]  [2, 1, 2, 2]   
2022-01-01 00:30:00                  [0, 0, 0, 0]  [2, 1, 1, 2]   
2022-01-01 00:45:00                  [0, 0, 0, 0]  [2, 1, 1, 2]   
2022-01-01 01:00:00                  [0, 0, 0, 0]  [2, 2, 1, 2]   
...                                           ...           ...   
2022-06-06 04:45:00  [10074, 10075, 10072, 10073]  [1, 2, 1, 1]   
2022-06-06 05:00:00  [10074, 10075, 10072, 10073]  [1, 2, 1, 1]   
2022-06-06 05:15:00  [10074, 10075, 10072, 10073]  [1, 2, 1, 1]   
2022-06-06 05:30:00  [10074, 10075, 10072, 10073]  [1, 2, 1, 1]   
2022-06-06 05:45:00  [10074, 10075, 10072, 10073]  [1, 2, 1, 1]   

                                       mask_truth  ev_charged_pwr  \
time                                                                
2022-01-01 00:00:00   [True, False, False, False]        0.000000   
2022-01-01 00:15:00  [False, False, False, False]        2.861465   
2022-01-01 00:30:00  [False, False, False, False]        0.000000   
2022-01-01 00:45:00  [False, False, False, False]        0.000000   
2022-01-01 01:00:00  [False, False, False, False]        0.000000   
...                                           ...             ...   
2022-06-06 04:45:00    [True, False, True, False]       11.936774   
2022-06-06 05:00:00    [True, False, True, False]       15.253757   
2022-06-06 05:15:00    [True, False, True, False]       15.844272   
2022-06-06 05:30:00    [True, False, True, False]       13.475763   
2022-06-06 05:45:00    [True, False, True, False]        9.859811   

                     ev_discharged_pwr          load  load_reward   EV_reward  \
time                                                                            
2022-01-01 00:00:00                0.0 -2.711875e+00    15.000000 -107.541622   
2022-01-01 00:15:00                0.0  0.000000e+00    -5.800165    0.000000   
2022-01-01 00:30:00                0.0 -4.880182e+00    -4.511270    0.000000   
2022-01-01 00:45:00                0.0 -3.706762e+00    -6.310984    0.000000   
2022-01-01 01:00:00                0.0 -5.442083e+00    -5.774037    0.000000   
...                                ...           ...          ...         ...   
2022-06-06 04:45:00               -1.0  0.000000e+00    15.000000    0.000000   
2022-06-06 05:00:00               -1.0  0.000000e+00    15.000000    0.000000   
2022-06-06 05:15:00               -1.0  1.776357e-15    -1.667302    0.000000   
2022-06-06 05:30:00               -1.0 -2.000381e+00    -5.845357    0.000000   
2022-06-06 05:45:00               -1.0 -4.929893e+00    -6.247568    0.000000   

                       rewards  
time                            
2022-01-01 00:00:00 -92.541622  
2022-01-01 00:15:00  -5.800165  
2022-01-01 00:30:00  -4.511270  
2022-01-01 00:45:00  -6.310984  
2022-01-01 01:00:00  -5.774037  
...                        ...  
2022-06-06 04:45:00  15.000000  
2022-06-06 05:00:00  15.000000  
202

In [ ]:
env.plot_VPP_results()


Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Training dataset VPP Simulation using the loaded trained model

In [ ]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 10956, Arrival time: 2022-01-01 07:30:00, Parking_time: 24, Leaving_time: 2022-01-02 07:30:00, SOC: 0.35945707857541814, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 12520, Arrival time: 2022-12-31 20:15:00, Parking_time: 22.216722711640834, Leaving_time: 2023-01-01 18:28:00.201762, SOC: 0.40255616230738644, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -34117.7 , over-consume=kWh  1556.25 , under-consume=kWh  -35673.95 , Total_cost=€  -1196.64 , overcost=€  97.86
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  18043.95 , over-consume=kWh  39659.07 , under-consume=kWh  21615.12 , Total_cost=€  871.32 , overcost=€  1659.78 , Charging_events=  1565 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  72.79


In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [ ]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  17368.58 , over-consume=kWh  39032.96 , under-consume=kWh  21664.39 , Total_cost=€  849.76 , overcost=€  1645.46 , Av.EV_en_left=kWh  100.0 , Charging_events=  1565 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  72.79
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -4801.56 , over-consume=KWh  624.98 , under-consume=KWh  5426.54 , Total_cost=€  -157.97 , Overcost=€  25.94 
 EV_INFO: Av.EV_energy_leaving=kWh  69.34 , Std.EV_energy_leaving=kWh  23.49 , EV_departures =  1558 , EV_queue_left =  3
SCORE:  Cumulative_reward= 491279.68 - Step_rewars (load_t= 410260.26, EVs_energy_t= 37040.84)
 - Final_rewards (EVs_energy= 23932.11, Overconsume= 3988.45, Underconsume= -946.54, Overcost= 17004.56)
Episode:1 Score:491279.6759246705


In [ ]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
VPP_table.head(14995)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:15:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:30:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:45:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 01:00:00   0.000000   0.000000   0.000000   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 03:30:00  58.639488  51.191147  38.674213  64.730286   
2022-06-06 03:45:00  59.236042  50.941147  38.424213  65.326836   
2022-06-06 04:00:00  60.361752  50.691147  38.174213  66.452545   
2022-06-06 04:15:00  60.984062  50.441147  38.796524  67.074860   
2022-06-06 04:30:00  61.630417  50.191147  39.442879  67.721214   

                                           EVs_id       actions  \
time                                                              
2022-01-01 00:00:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 01:00:00                  [0, 0, 0, 0]  [2, 0, 1, 0]   
...                                           ...           ...   
2022-06-06 03:30:00  [14771, 14770, 14768, 14769]  [1, 2, 2, 1]   
2022-06-06 03:45:00  [14771, 14770, 14768, 14769]  [1, 2, 2, 1]   
2022-06-06 04:00:00  [14771, 14770, 14768, 14769]  [1, 2, 1, 1]   
2022-06-06 04:15:00  [14771, 14770, 14768, 14769]  [1, 2, 1, 1]   
2022-06-06 04:30:00  [14771, 14770, 14768, 14769]  [1, 2, 1, 1]   

                                      mask_truth  ev_charged_pwr  \
time                                                               
2022-01-01 00:00:00  [False, False, False, True]        0.000000   
2022-01-01 00:15:00  [False, False, False, True]        0.000000   
2022-01-01 00:30:00  [False, False, False, True]        0.000000   
2022-01-01 00:45:00  [False, False, False, True]        0.000000   
2022-01-01 01:00:00   [False, True, False, True]        0.000000   
...                                          ...             ...   
2022-06-06 03:30:00   [True, False, False, True]        5.777786   
2022-06-06 03:45:00   [True, False, False, True]        4.772425   
2022-06-06 04:00:00    [True, False, True, True]        9.005691   
2022-06-06 04:15:00    [True, False, True, True]        7.467731   
2022-06-06 04:30:00    [True, False, True, True]        7.756264   

                     ev_discharged_pwr          load  load_reward  EV_reward  \
time                                                                           
2022-01-01 00:00:00                0.0 -4.675910e+00    -3.843485        0.0   
2022-01-01 00:15:00                0.0 -3.306091e+00    -4.794330        0.0   
2022-01-01 00:30:00                0.0 -3.876598e+00    -3.677138        0.0   
2022-01-01 00:45:00                0.0 -3.206283e+00    -6.094718        0.0   
2022-01-01 01:00:00                0.0 -5.204189e+00    -5.886800        0.0   
...                                ...           ...          ...        ...   
2022-06-06 03:30:00               -2.0 -4.440892e-16    15.000000        0.0   
2022-06-06 03:45:00               -2.0  0.000000e+00    15.000000        0.0   
2022-06-06 04:00:00               -2.0  0.000000e+00    15.000000        0.0   
2022-06-06 04:15:00               -1.0 -8.881784e-16    15.000000        0.0   
2022-06-06 04:30:00               -1.0  0.000000e+00    15.000000        0.0   

                       rewards  
time                            
2022-01-01 00:00:00  -3.843485  
2022-01-01 00:15:00  -4.794330  
2022-01-01 00:30:00  -3.677138  
2022-01-01 00:45:00  -6.094718  
2022-01-01 01:00:00  -5.886800  
...                        ...  
2022-06-06 03:30:00  15.000000  
2022-06-06 03:45:00  15.000000  
2022-06-06 04:00:00  15.00000

In [ ]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_actions_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
#env.close()